Notebook for the one-hot autoencoder

In [1]:
from communications import *
from model import *
import numpy as np
import matplotlib.pyplot as plt
import os.path

%load_ext autoreload
%autoreload 2

In [2]:
import pickle

def save_obj(obj, name ):
    with open(name + '.pkl', 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

def load_obj(name ):
    with open(name + '.pkl', 'rb') as f:
        return pickle.load(f)

In [3]:
X_train,y_train=np.eye(256),np.eye(256)

In [4]:
SNR=3
add_name='_3_new'

In [ ]:
autoencoderAWGN,encoderAWGN,decoderAWGN=OHAutoencoder(5*256,5*256,AWGN,SNR,use_BN=False,use_LN=False)

In [5]:
boundaries = [2**16,2**17]
values = [1e-4,1e-5,1e-6]
lr_schedule = tf.keras.optimizers.schedules.PiecewiseConstantDecay(boundaries, values)
autoencoderAWGN,encoderAWGN,decoderAWGN=OHAutoencoder2(5*256,5*256,AWGN,SNR,use_BN=True,use_LN=False,lr=1e-4,encoder_activation='tanh',hidden_activation='relu',optim=Adam,lookahead=False,gradient_centralization=False)

In [ ]:
autoencoderAWGN,encoderAWGN,decoderAWGN=OHAutoencoder(5*256,5*256,multi_AWGN,use_BN=False,use_LN=False)

In [ ]:
from tensorflow.keras.models import load_model

encoderAWGN,decoderAWGN=load_model('AWGNOHEncoder_3_test.h5',custom_objects={'AWGN':AWGN}),load_model('AWGNOHDecoder_3_test.h5',custom_objects={'AWGN':AWGN})
autoencoderAWGN,encoderAWGN,decoderAWGN=recompile(encoderAWGN,decoderAWGN,AWGN,noise_param=SNR,optim=Adam,lookahead=True,gradient_centralization=True,lr=1e-6)

In [5]:
def schedule(epoch,lr):
    if epoch<2**9:
        return 1e-3
    if epoch<3*2**16:
        return 1e-5
    else:
        return 1e-6
    

scheduler=tf.keras.callbacks.LearningRateScheduler(schedule)


In [6]:
boundaries = [2**16,2**17]
values = [1e-4,1e-5,1e-6]
lr_schedule = tf.keras.optimizers.schedules.PiecewiseConstantDecay(boundaries, values)
autoencoderAWGN,encoderAWGN,decoderAWGN=OHAutoencoder2(5*256,5*256,AWGN,SNR,use_BN=True,use_LN=False,lr=1e-4,encoder_activation='tanh',hidden_activation=mish,optim=RectifiedAdam,lookahead=True,gradient_centralization=True)

In [ ]:
checkpoint=tf.keras.callbacks.ModelCheckpoint('AWGNOHAutoencoder'+add_name+'.h5',monitor='loss',save_best_only=True)
history=autoencoderAWGN.fit(x=X_train,y=y_train,batch_size=256,epochs=2**18,callbacks=[checkpoint,scheduler],verbose=2)
save_obj(history.history,'history'+add_name)
encoderAWGN.save('AWGNOHEncoder'+add_name+'.h5')
decoderAWGN.save('AWGNOHDecoder'+add_name+'.h5')

Epoch 1/262144
Instructions for updating:
If using Keras pass *_constraint arguments to layers.
1/1 - 0s - loss: 6.3276 - ber_metric_oh: 0.4868 - acc: 0.0000e+00 - lr: 0.0010
Epoch 2/262144
1/1 - 0s - loss: 6.3196 - ber_metric_oh: 0.5000 - acc: 0.0000e+00 - lr: 0.0010
Epoch 3/262144
1/1 - 0s - loss: 6.3134 - ber_metric_oh: 0.5044 - acc: 0.0000e+00 - lr: 0.0010
Epoch 4/262144
1/1 - 0s - loss: 6.2974 - ber_metric_oh: 0.4951 - acc: 0.0117 - lr: 0.0010
Epoch 5/262144
1/1 - 0s - loss: 6.2709 - ber_metric_oh: 0.4868 - acc: 0.0039 - lr: 0.0010
Epoch 6/262144
1/1 - 0s - loss: 6.2737 - ber_metric_oh: 0.5103 - acc: 0.0039 - lr: 0.0010
Epoch 7/262144
1/1 - 0s - loss: 6.2055 - ber_metric_oh: 0.4932 - acc: 0.0000e+00 - lr: 0.0010
Epoch 8/262144
1/1 - 0s - loss: 6.2123 - ber_metric_oh: 0.5034 - acc: 0.0000e+00 - lr: 0.0010
Epoch 9/262144
1/1 - 0s - loss: 6.1011 - ber_metric_oh: 0.4990 - acc: 0.0039 - lr: 0.0010
Epoch 10/262144
1/1 - 0s - loss: 6.0264 - ber_metric_oh: 0.4717 - acc: 0.0078 - lr: 0.001

Epoch 87/262144
1/1 - 0s - loss: 1.6410 - ber_metric_oh: 0.0493 - acc: 0.9023 - lr: 0.0010
Epoch 88/262144
1/1 - 0s - loss: 1.5706 - ber_metric_oh: 0.0591 - acc: 0.8828 - lr: 0.0010
Epoch 89/262144
1/1 - 0s - loss: 1.5414 - ber_metric_oh: 0.0532 - acc: 0.8906 - lr: 0.0010
Epoch 90/262144
1/1 - 0s - loss: 1.4594 - ber_metric_oh: 0.0474 - acc: 0.8945 - lr: 0.0010
Epoch 91/262144
1/1 - 0s - loss: 1.4901 - ber_metric_oh: 0.0288 - acc: 0.9375 - lr: 0.0010
Epoch 92/262144
1/1 - 0s - loss: 1.4449 - ber_metric_oh: 0.0366 - acc: 0.9297 - lr: 0.0010
Epoch 93/262144
1/1 - 0s - loss: 1.4817 - ber_metric_oh: 0.0425 - acc: 0.9102 - lr: 0.0010
Epoch 94/262144
1/1 - 0s - loss: 1.4828 - ber_metric_oh: 0.0532 - acc: 0.8906 - lr: 0.0010
Epoch 95/262144
1/1 - 0s - loss: 1.3874 - ber_metric_oh: 0.0474 - acc: 0.9023 - lr: 0.0010
Epoch 96/262144
1/1 - 0s - loss: 1.3586 - ber_metric_oh: 0.0474 - acc: 0.9023 - lr: 0.0010
Epoch 97/262144
1/1 - 0s - loss: 1.3463 - ber_metric_oh: 0.0254 - acc: 0.9492 - lr: 0.0010

Epoch 177/262144
1/1 - 0s - loss: 0.4220 - ber_metric_oh: 0.0107 - acc: 0.9805 - lr: 0.0010
Epoch 178/262144
1/1 - 0s - loss: 0.4382 - ber_metric_oh: 0.0151 - acc: 0.9727 - lr: 0.0010
Epoch 179/262144
1/1 - 0s - loss: 0.4275 - ber_metric_oh: 0.0078 - acc: 0.9844 - lr: 0.0010
Epoch 180/262144
1/1 - 0s - loss: 0.3972 - ber_metric_oh: 0.0103 - acc: 0.9844 - lr: 0.0010
Epoch 181/262144
1/1 - 0s - loss: 0.3829 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 182/262144
1/1 - 0s - loss: 0.3854 - ber_metric_oh: 0.0020 - acc: 0.9961 - lr: 0.0010
Epoch 183/262144
1/1 - 0s - loss: 0.3738 - ber_metric_oh: 0.0083 - acc: 0.9844 - lr: 0.0010
Epoch 184/262144
1/1 - 0s - loss: 0.3874 - ber_metric_oh: 0.0059 - acc: 0.9883 - lr: 0.0010
Epoch 185/262144
1/1 - 0s - loss: 0.3705 - ber_metric_oh: 0.0034 - acc: 0.9922 - lr: 0.0010
Epoch 186/262144
1/1 - 0s - loss: 0.3646 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 187/262144
1/1 - 0s - loss: 0.3544 - ber_metric_oh: 0.0054 - acc: 

Epoch 266/262144
1/1 - 0s - loss: 0.1755 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 267/262144
1/1 - 0s - loss: 0.2030 - ber_metric_oh: 0.0054 - acc: 0.9883 - lr: 0.0010
Epoch 268/262144
1/1 - 0s - loss: 0.2183 - ber_metric_oh: 0.0078 - acc: 0.9844 - lr: 0.0010
Epoch 269/262144
1/1 - 0s - loss: 0.2036 - ber_metric_oh: 0.0020 - acc: 0.9961 - lr: 0.0010
Epoch 270/262144
1/1 - 0s - loss: 0.1971 - ber_metric_oh: 0.0039 - acc: 0.9922 - lr: 0.0010
Epoch 271/262144
1/1 - 0s - loss: 0.1678 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 272/262144
1/1 - 0s - loss: 0.1707 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 273/262144
1/1 - 0s - loss: 0.1852 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 274/262144
1/1 - 0s - loss: 0.1788 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 275/262144
1/1 - 0s - loss: 0.1928 - ber_metric_oh: 0.0034 - acc: 0.9922 - lr: 0.0010
Epoch 276/262144
1/1 - 0s - loss: 0.1764 - ber_metric_oh: 0.

Epoch 354/262144
1/1 - 0s - loss: 0.1104 - ber_metric_oh: 0.0034 - acc: 0.9922 - lr: 0.0010
Epoch 355/262144
1/1 - 0s - loss: 0.0916 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 356/262144
1/1 - 0s - loss: 0.0907 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 357/262144
1/1 - 0s - loss: 0.1231 - ber_metric_oh: 0.0054 - acc: 0.9922 - lr: 0.0010
Epoch 358/262144
1/1 - 0s - loss: 0.1097 - ber_metric_oh: 0.0020 - acc: 0.9961 - lr: 0.0010
Epoch 359/262144
1/1 - 0s - loss: 0.1272 - ber_metric_oh: 0.0049 - acc: 0.9883 - lr: 0.0010
Epoch 360/262144
1/1 - 0s - loss: 0.1450 - ber_metric_oh: 0.0078 - acc: 0.9844 - lr: 0.0010
Epoch 361/262144
1/1 - 0s - loss: 0.0936 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 362/262144
1/1 - 0s - loss: 0.0922 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 0.0010
Epoch 363/262144
1/1 - 0s - loss: 0.1191 - ber_metric_oh: 0.0063 - acc: 0.9883 - lr: 0.0010
Epoch 364/262144
1/1 - 0s - loss: 0.1308 - ber_metric_oh: 0.0020

...

1/1 - 0s - loss: 0.0019 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71651/262144
1/1 - 0s - loss: 0.0043 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71652/262144
1/1 - 0s - loss: 0.0021 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71653/262144
1/1 - 0s - loss: 0.0097 - ber_metric_oh: 0.0024 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71654/262144
1/1 - 0s - loss: 0.0098 - ber_metric_oh: 0.0049 - acc: 0.9922 - lr: 1.0000e-05
Epoch 71655/262144
1/1 - 0s - loss: 0.0059 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71656/262144
1/1 - 0s - loss: 0.0100 - ber_metric_oh: 0.0024 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71657/262144
1/1 - 0s - loss: 0.0044 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71658/262144
1/1 - 0s - loss: 0.0059 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71659/262144
1/1 - 0s - loss: 0.0085 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71660

Epoch 71731/262144
1/1 - 0s - loss: 0.0043 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71732/262144
1/1 - 0s - loss: 0.0076 - ber_metric_oh: 0.0029 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71733/262144
1/1 - 0s - loss: 0.0060 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71734/262144
1/1 - 0s - loss: 0.0101 - ber_metric_oh: 0.0024 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71735/262144
1/1 - 0s - loss: 0.0048 - ber_metric_oh: 4.8828e-04 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71736/262144
1/1 - 0s - loss: 0.0058 - ber_metric_oh: 0.0020 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71737/262144
1/1 - 0s - loss: 0.0026 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71738/262144
1/1 - 0s - loss: 0.0021 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71739/262144
1/1 - 0s - loss: 0.0065 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71740/262144
1/1 - 0s - loss: 0.0020 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0

Epoch 71812/262144
1/1 - 0s - loss: 0.0049 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71813/262144
1/1 - 0s - loss: 0.0028 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71814/262144
1/1 - 0s - loss: 0.0036 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71815/262144
1/1 - 0s - loss: 0.0027 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71816/262144
1/1 - 0s - loss: 0.0077 - ber_metric_oh: 0.0024 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71817/262144
1/1 - 0s - loss: 0.0031 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71818/262144
1/1 - 0s - loss: 0.0020 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71819/262144
1/1 - 0s - loss: 0.0028 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71820/262144
1/1 - 0s - loss: 0.0118 - ber_metric_oh: 4.8828e-04 - acc: 0.9961 - lr: 1.0000e-05
Epoch 71821/262144
1/1 - 0s - loss: 0.0072 - ber_metric_oh: 0.0020 - acc: 0.9961 - lr:

Epoch 71893/262144
1/1 - 0s - loss: 0.0019 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71894/262144
1/1 - 0s - loss: 0.0040 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71895/262144
1/1 - 0s - loss: 0.0039 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71896/262144
1/1 - 0s - loss: 0.0034 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71897/262144
1/1 - 0s - loss: 0.0030 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71898/262144
1/1 - 0s - loss: 0.0053 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71899/262144
1/1 - 0s - loss: 0.0026 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71900/262144
1/1 - 0s - loss: 0.0031 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71901/262144
1/1 - 0s - loss: 0.0044 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71902/262144
1/1 - 0s - loss: 0.0035 - ber_metric_oh: 0.0000e+00 - acc: 1.00

Epoch 71974/262144
1/1 - 0s - loss: 0.0040 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05
Epoch 71975/262144
1/1 - 0s - loss: 0.0043 - ber_metric_oh: 0.0000e+00 - acc: 1.0000 - lr: 1.0000e-05


In [ ]:
computeVarianceAWGN(encoderAWGN,do_polar=True,print_code=True,round=True)

In [ ]:
testLinearAWGN(encoderAWGN)

In [ ]:
np.count_non_zero(np.round(encoderAWGN.predict(np.eye(256))))